## Problema rellenar una mochila sin valores

In [2]:
import numpy as np
from scipy.sparse import csr_matrix
import torch
from time import time
import sys

In [3]:
def tensor_generator(pesos:np.array, valores:np.array, n_elementos:np.array, capacidad:int, tao:float, lambda1:float):
    lista_de_tensores = []
    n_clases = len(pesos)
    inicio=time()
    tensor = tensor_initial_generator(pesos[0],valores[0],n_elementos[0],capacidad,0,tao)
    lista_de_tensores.append(tensor)
    fin = time()
    #print("tiempo creacion primr tensor", fin-inicio)
    
    inicio2=time()
    for n in range(1, n_clases-1):
        tensor = tensor_intermediate_generator(pesos[n], valores[n], n_elementos[n], capacidad, tensor.shape[1],tao)
        lista_de_tensores.append(tensor)
    fin2 = time()
    #print("tiempo creacion segundo tensor", fin2-inicio2)
    inicio3=time()
    tensor = tensor_final_generator(pesos[-1], valores[-1], n_elementos[-1], capacidad, tensor.shape[1],tao, lambda1)

    lista_de_tensores.append(tensor)
    fin3 = time()
    #print("tiempo creacion segundo tensor", fin3-inicio3)
    return lista_de_tensores



In [4]:
def tensor_initial_generator(peso:int, valor:int, n_elementos:int, capacidad:int, previous_weight_solution:int,tao)->np.array:
    """
    Funcion que genera el tensor inicial.
    """
    tamaño_1 = min((capacidad-previous_weight_solution)//peso,n_elementos)+1
    tamaño_2 = min(capacidad, (tamaño_1-1)*peso+previous_weight_solution)+1
    tensor = np.zeros((tamaño_1,tamaño_2))
    for i in range(tamaño_1):
        elemento = i*peso + previous_weight_solution
        tensor[i][elemento] = valor**i
    
    return csr_matrix(tensor)

In [5]:

def tensor_intermediate_generator(peso: int, valor: int, n_elementos: int, capacidad: int, previous_weight: int, tao: float) -> csr_matrix:
    """
    Genera el tensor intermedio optimizado como una matriz dispersa (sparse) en formato CSR.
    """
    # Dimensiones del tensor
    tamaño_1 = previous_weight
    tamaño_2 = min(capacidad, n_elementos * peso + previous_weight - 1) + 1
    
    # Variables para almacenar los índices de los elementos no nulos y sus valores
    row_indices = []
    col_indices = []
    data = []

    # Vectorización para calcular las posiciones y valores no nulos
    for i in range(tamaño_1):
        n_elementos_restantes = min((capacidad - i) // peso, n_elementos) + 1
        j_values = np.arange(n_elementos_restantes)
        elemento_indices = i + j_values * peso
        valores = valor**j_values
        
        # Añadir los valores calculados a las listas
        row_indices.extend([i] * n_elementos_restantes)
        col_indices.extend(elemento_indices)
        data.extend(valores)

    # Crear la matriz dispersa directamente con los índices y valores calculados
    tensor = csr_matrix((data, (row_indices, col_indices)), shape=(tamaño_1, tamaño_2))

    return tensor


In [6]:
def tensor_final_generator(peso:int, valor:int,n_elementos: int, capacidad: int, previous_weight:int, tao:float, lambda1:float)->np.array:
    tamaño_1 = previous_weight
    tensor = np.zeros((tamaño_1))
    for i in range(tamaño_1):
        n_elementos_posibles = min((capacidad -i)//peso,n_elementos)+1

        for j in range(n_elementos_posibles):
            
            tensor[i] += valor**j
            #tensor[i] += np.exp(-tao*(capacidad - elemento))
            #tensor[i] += np.exp(-lambda1*(capacidad - elemento))
            
    return csr_matrix(tensor)

In [50]:
'''
def tensor_contraction(lista_de_tensores:list):

    n_tensores = len(lista_de_tensores)
    tensores_intermedios = []
    vector = lista_de_tensores[-1]
    tensores_intermedios.append(vector)
    for j in range(n_tensores-1,0,-1):
        if j==n_tensores-1:
            vector = lista_de_tensores[j-1] @ vector.T
        else:
            vector = lista_de_tensores[j-1] @ vector
        if max(vector) > 1e200:
            vector = vector*1e-15
        tensores_intermedios.append(vector)
    tensores_intermedios.reverse()
    return vector,tensores_intermedios
'''


import torch
from scipy.sparse import csr_matrix

def tensor_contraction(lista_de_tensores):
    n_tensores = len(lista_de_tensores)
    tensores_intermedios = []

    # Iniciar el vector como el último tensor en la lista, convertido temporalmente a PyTorch en la GPU
    vector = torch.tensor(lista_de_tensores[-1].toarray(), device='cuda')
    tensores_intermedios.append(csr_matrix(vector.cpu().numpy()))  # Guardamos en formato sparse en CPU

    # Realizar la contracción de tensores uno por uno
    for j in range(n_tensores - 1, 0, -1):
        # Convertir el tensor actual a formato denso de PyTorch temporalmente
        current_tensor = torch.tensor(lista_de_tensores[j - 1].toarray(), device='cuda')
        
        # Realizar la multiplicación y almacenar el resultado temporalmente en GPU
        if j == n_tensores - 1:
            vector = current_tensor @ vector.T
        else:
            vector = current_tensor @ vector
  
        # Normalización si es necesario para evitar overflow
        if torch.max(vector) > 1e200:
           vector = vector * 1e-15
   
        # Guardar el resultado intermedio como un tensor disperso en CPU
        tensores_intermedios.append(csr_matrix(vector.cpu().numpy()))
    
    # Convertir la lista de tensores intermedios de nuevo a formato CPU y retornar el último vector en CPU
    vector = csr_matrix(vector.cpu().numpy())
    tensores_intermedios.reverse()
    
    return vector, tensores_intermedios

In [44]:
from os import listxattr
from time import time

def solver(pesos:np.array, valores:np.array, n_elementos:np.array, capacidad:int, tao:float, lambda1:float)->np.array:
    """
    Funcion que resuelve el problema de la mochila sin valores.
    """ 
    valores2 = np.exp(valores*tao)
    n_clases = len(pesos)
    solution = np.zeros(n_clases)
   
    lista_de_tensores = tensor_generator(pesos, valores2, n_elementos, capacidad, tao, lambda1)


    vector_salida, tensores_intermedios = tensor_contraction(lista_de_tensores)


    max = np.max(tensores_intermedios[0])
    solution[0] = np.argmax(vector_salida)
    
  
    for n in range(1,n_clases-1):
        cuenta_peso = int(np.dot(solution[:n],pesos[:n]))
       
        new_initial_tensor = tensor_initial_generator(pesos[n], valores2[n], n_elementos[n], capacidad, cuenta_peso,tao)


        if n==n_clases-2:
            tensores_intermedios[n+1]=tensores_intermedios[n+1].T
            solution[n]= np.argmax(new_initial_tensor @ tensores_intermedios[n+1][:new_initial_tensor.shape[1]])
        else:
            solution[n]= np.argmax(new_initial_tensor @ tensores_intermedios[n+1][:new_initial_tensor.shape[1]])

    cuenta_peso = np.dot(solution[:-1],pesos[:-1])
    solution[-1] = min((capacidad-cuenta_peso)//pesos[-1],n_elementos[-1])
    resto = capacidad - np.dot(solution,pesos)

    #print("La solucion es: ", solution)
    print("El peso total es: ", np.dot(solution,pesos))
    print("El valor total es: ", np.dot(solution,valores))
    return np.dot(solution,pesos),np.dot(solution,valores),max

In [51]:


clases = 1000
capacidad = 2343
np.random.seed(1)
pesos = np.random.randint(1,10,clases)

valores = np.random.rand(clases)

n_elementos = [1]*clases



tao = 10
lambda1 = 1


b=solver(pesos,valores, n_elementos, capacidad, tao, lambda1)



El peso total es:  2341.0
El valor total es:  396.8078540647915


In [10]:
def mochila_greedy(pesos, valores, capacidad, n_elementos):
    n_clases = len(pesos)
    
    # Calculamos la relación valor/peso para cada clase
    valor_peso = valores / pesos
    
    # Ordenamos los elementos por su valor/peso de mayor a menor
    indices_ordenados = np.argsort(valor_peso)[::-1]  # Orden descendente
    
    # Inicializamos variables
    peso_actual = 0
    valor_actual = 0
    solucion = np.zeros(n_clases, dtype=int)
    
    # Recorremos los objetos en orden greedy
    for i in indices_ordenados:
        # Tomamos la mayor cantidad posible de este objeto sin exceder la capacidad
        cantidad = min(n_elementos[i], (capacidad - peso_actual) // pesos[i])
        solucion[i] = cantidad
        peso_actual += cantidad * pesos[i]
        valor_actual += cantidad * valores[i]
        
        # Si llenamos la capacidad, salimos del bucle
        if peso_actual >= capacidad:
            break
    
    return solucion, valor_actual

# Ejecutamos el algoritmo

mejor_solucion, mejor_valor = mochila_greedy(pesos, valores, capacidad, n_elementos)

print("Mejor solución encontrada (greedy):", mejor_solucion)
print("Valor total de la mejor solución (greedy):", mejor_valor)
print("Peso total de la mejor solución (greedy):", np.sum(mejor_solucion * pesos))

Mejor solución encontrada (greedy): [0 0 0 3 0 3 0 2 0 0]
Valor total de la mejor solución (greedy): 5.763134496599547
Peso total de la mejor solución (greedy): 23


In [11]:
import matplotlib.pyplot as plt
import random
from time import time
def guardar_experimento(nombre_archivo, descripcion_experimento, precision,tao, max_values,timet,capacity):
    with open(nombre_archivo, 'a') as file:
        file.write(f"Descripción del experimento: {descripcion_experimento}\n")
        file.write(f"Precisión: {precision}\n")
        file.write(f"Valores tao: {tao}\n")
        file.write(f"Valores máximos: {max_values}\n")
        file.write(f"tiempos: {timet}\n")
        file.write(f"capacidad: {capacity}\n")
        file.write("="*40 + "\n")
        
def tao_experimento(clases,capacidad,pesos,valores,n_elementos,tao,lambda1,experimento):
   precision=[]
   max_values=[]
   time = []
   for t in tao:
      inicio = time()
      p1,v1,max=solver(pesos,valores,n_elementos,capacidad,t,lambda1)
      fin = time()
      tiempo = fin-inicio
      p2,v2 = mochila_greedy(pesos,valores,capacidad,n_elementos)
      time.append(tiempo)
      precision.append(v1/v2)
      max_values.append(max)
   random_color = (random.random(), random.random(), random.random())
   plt.plot(tao, precision, marker='o', color=random_color, linestyle='-')  # 'o' para puntos, 'b' para color azul, '-' para línea sólida
   plt.axhline(y=1, color='gray', linestyle='--', linewidth=0.8)
   # Añadir etiquetas y título
   plt.xlabel(r"$\tau$")
   plt.ylabel("precision")
   plt.title("Gráfico de línea con dos listas")
   #plt.savefig(f"grafico_precision_{experimento}.png", format="png", dpi=300)
   nombre_archivo = f"resultados_experimentos.txt"
   descripcion_experimento = f"Experimento {experimento}, clases={clases} con min_tao={tao[0]} ,max_tao={tao[-1]},capacidad={int(0.75*(clases)*n_elementos[0])},n_elementos={n_elementos}, tiempo ={time}"
   guardar_experimento(nombre_archivo, descripcion_experimento, precision,tao, max_values,capacity)
   return precision,max_values



In [12]:

clases = 1

np.random.seed(1)

capacidad = int(0.75*(clases)*n_elementos[0])
tao = np.linspace(0,8,12)

lambda1 = 0
exp=1
lastexp=10
'''
for exp in range(1,lastexp):
    clases = exp*400+400
    pesos = np.random.randint(1,10,clases)
    capacidad = int(0.75*(clases)*n_elementos[0])
    valores = np.random.rand(clases)
    n_elementos = [9]*clases
    precision,max_values=tao_experimento(clases,capacidad,pesos,valores,n_elementos,tao,lambda1,exp)
'''

'\nfor exp in range(1,lastexp):\n    clases = exp*400+400\n    pesos = np.random.randint(1,10,clases)\n    capacidad = int(0.75*(clases)*n_elementos[0])\n    valores = np.random.rand(clases)\n    n_elementos = [9]*clases\n    precision,max_values=tao_experimento(clases,capacidad,pesos,valores,n_elementos,tao,lambda1,exp)\n'

In [13]:
from time import time
np.random.seed(1)

capacidad = int(0.75*(clases)*n_elementos[0])
tao = np.linspace(0,8,12)
timet = []
clase = []
capacity = []
lambda1 = 0
exp=1
tao = 5
lastexp=15
for exp in range(1,lastexp):
    clases = 1000
    
    pesos = np.random.randint(1,10,clases)
    capacidad = int(exp*0.1*(clases)*n_elementos[0])
    capacity.append(capacidad)
    valores = np.random.rand(clases)
    n_elementos = [9]*clases
    inicio=time()
    precision,max_values,max=solver(pesos,valores,n_elementos,capacidad,tao,lambda1)
    fin = time()
    tiempo = fin-inicio
    timet.append(tiempo)

random_color = (random.random(), random.random(), random.random())
plt.plot(capacity, timet, marker='o', color=random_color, linestyle='-')  # 'o' para puntos, 'b' para color azul, '-' para línea sólida
plt.axhline(y=1, color='gray', linestyle='--', linewidth=0.8)
# Añadir etiquetas y título
plt.xlabel("capacidad en porciento")
plt.ylabel("tiempo")
plt.title("Gráfico de línea con dos listas")
#plt.savefig(f"grafico_precision_{experimento}.png", format="png", dpi=300)
nombre_archivo = f"resultados_experimentos.txt"
descripcion_experimento = f"Experimento tiempo en función de clase, clases={clases} con tao={tao},capacidad={capacidad},n_elementos={n_elementos}, tiempo ={timet}"
guardar_experimento(nombre_archivo, descripcion_experimento, precision,tao, max_values, timet,capacity)

t
  (0, 0)	1.0
  (1, 6)	1.1531003224793381
  (2, 12)	1.3296403537019537
  (3, 18)	1.5332087206352638
  (4, 24)	1.7679434701926562
  (5, 30)	2.038616185604392
  (6, 36)	2.350728981032023
  (7, 42)	2.710626346089551
  (8, 48)	3.1256241137968517
  (9, 54)	3.604158173568345
t
  (0, 0)	1.0
  (0, 9)	25.05717213674184
  (0, 18)	627.8618754903116
  (0, 27)	15732.443092258312
  (0, 36)	394210.5346942116
  (0, 45)	9877801.225949902
  (0, 54)	247509765.65114626
  (0, 63)	6201894803.445405
  (0, 72)	155401945663.8962
  (0, 81)	3893933302884.8496
  (1, 1)	1.0
  (1, 10)	25.05717213674184
  (1, 19)	627.8618754903116
  (1, 28)	15732.443092258312
  (1, 37)	394210.5346942116
  (1, 46)	9877801.225949902
  (1, 55)	247509765.65114626
  (1, 64)	6201894803.445405
  (1, 73)	155401945663.8962
  (1, 82)	3893933302884.8496
  (2, 2)	1.0
  (2, 11)	25.05717213674184
  (2, 20)	627.8618754903116
  (2, 29)	15732.443092258312
  (2, 38)	394210.5346942116
  :	:
  (52, 97)	9877801.225949902
  (52, 106)	247509765.65114626


KeyboardInterrupt: 

In [ ]:
import matplotlib.pyplot as plt
from time import time
tao=0.5
num_clases=np.arange(10,11)
tiempo=[]
precision=[]
for j in num_clases:
    pesos = np.random.randint(1,10,j)
    n_elementos = [3]*j
    capacidad = j*10
    inicio=time()
    b=solver(pesos, n_elementos, capacidad, tao)
    resultado=np.dot(b,pesos)
    fin=time()
    tiempo.append(fin-inicio)
    precision.append(resultado/capacidad)



plt.plot(num_clases, precision, marker='o', color='b', linestyle='-')  # 'o' para puntos, 'b' para color azul, '-' para línea sólida

# Añadir etiquetas y título
plt.xlabel("num_clases")
plt.ylabel("tiempo")
plt.title("Gráfico de línea con dos listas")

# Mostrar el gráfico
plt.show()

TypeError: solver() missing 2 required positional arguments: 'tao' and 'lambda1'

In [ ]:
with open('/home/sergio/simulador/Simulador_Cuantica/quantum-sim/TensorNetwork/knapsackProblemInstances/problemInstances/n_400_c_1000000_g_2_f_0.1_eps_0_s_100/test.in', 'r') as file:
    n = int(file.readline().strip())
    
    # Inicializar las listas de valores y pesos
    valores = []
    pesos = []
    
    # Leer los valores y pesos de cada objeto
    for _ in range(n):
        id_objeto, valor, peso = map(int, file.readline().split())
        valores.append(valor)
        pesos.append(peso)
    
    # Leer la capacidad de la mochila
    capacidad = int(file.readline().strip())

# Mostrar los resultados
print(f"n (Número de objetos): {n}")
print(f"Pesos de los objetos: {pesos}")
print(f"Valores de los objetos: {valores}")
print(f"Capacidad de la mochila: {capacidad}")

n (Número de objetos): 400
Pesos de los objetos: [500014, 500087, 500059, 500050, 500078, 500082, 500074, 500037, 500060, 500015, 500080, 500068, 500055, 500025, 500040, 500092, 500015, 500032, 500027, 500070, 500061, 500018, 500001, 500074, 500047, 500066, 500008, 500046, 500053, 500030, 500067, 500008, 500033, 500080, 500023, 500067, 500001, 500043, 500068, 500044, 500005, 500022, 500056, 500095, 500028, 500089, 500043, 500063, 500005, 500019, 500022, 500035, 500096, 500039, 500022, 500091, 500050, 500042, 500059, 500017, 500036, 500087, 500056, 500074, 500055, 500015, 500094, 500084, 500046, 500020, 500026, 500063, 500022, 500017, 500085, 500035, 500069, 500035, 500052, 500031, 500071, 500008, 500076, 500044, 500045, 500095, 500011, 500016, 500086, 500044, 500075, 500028, 500088, 500057, 500001, 500027, 500016, 500074, 500047, 500039, 500062, 500081, 500028, 500014, 500037, 500008, 500035, 500059, 500057, 500042, 500096, 500038, 500018, 500083, 500065, 500046, 500073, 500005, 500037